# Book Recommenmdation System

In a very general way, recommender systems are algorithms aimed at suggesting relevant items to users (items being movies to watch, text to read, products to buy, or anything else depending on industries).
Recommender systems are really critical in some industries as they can generate a huge amount of income when they are efficient or also be a way to stand out significantly from competitors. The main objective is to create a book recommendation system for users.

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
#Importinf Libraries
import pandas as pd
import sys
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import random
# This is to supress the warning messages (if any) generated in our code
import warnings
warnings.filterwarnings('ignore')


# Data
● Users :
Contains the users. Note that user IDs (User-ID) have been anonymized and map to integers. Demographic data is provided (Location, Age) if available. Otherwise, these fields contain NULL values.
● Books :
Books are identified by their respective ISBN. Invalid ISBNs have already been removed from the dataset. Moreover, some content-based information is given (Book-Title, Book-Author, Year-Of-Publication, Publisher), obtained from Amazon Web Services. Note that in the case of several authors, only the first is provided. URLs linking to cover images are also given, appearing in three different flavors (Image-URL-S, Image-URL-M, Image-URL-L), i.e., small, medium, large. These URLs point to the Amazon website.
● Ratings :
Contains the book rating information. Ratings (Book-Rating) are either explicit, expressed on a scale from 1-10 (higher values denoting higher appreciation), or implicit, expressed by 0.

# Importing Dataset

In [ ]:
#Users data
users = pd.read_csv('/content/drive/MyDrive/Book-Recommondation/Users.csv')
users.head()

In [ ]:
users.info()

In [ ]:
#Book data
books = pd.read_csv('/content/drive/MyDrive/Book-Recommondation/Books.csv')
books.head()

In [ ]:
#Rating data
ratings = pd.read_csv('/content/drive/MyDrive/Book-Recommondation/Ratings.csv')
ratings.head()

In [ ]:
# Dimension of Dataset


In [ ]:
users.shape,ratings.shape,books.shape

# 1) Users_dataset

In [ ]:
def missing_values(df):
    mis_val=df.isnull().sum()
    mis_val_percent=round(df.isnull().mean().mul(100),2)
    mz_table=pd.concat([mis_val,mis_val_percent],axis=1)
    mz_table=mz_table.rename(
    columns={df.index.name:'col_name',0:'Missing Values',1:'% of Total Values'})
    mz_table['Data_type']=df.dtypes
    mz_table=mz_table.sort_values('% of Total Values',ascending=False)
    return mz_table.reset_index()

In [ ]:
missing_values(users)

    Age have about 39% of missing values.

In [ ]:
#Age distribution

In [ ]:
users.Age.hist(bins=[0,10,20,30,40,50,100])
plt.title('Age Distribution')
plt.xlabel('Age')
plt.ylabel('Count')
plt.show()

The most active users are ampong those in their 20-40s of age

In [ ]:
#Outliers detection
sns.boxplot(y = 'Age', data= users)
plt.title('Find outlier data in Age column')

In [ ]:
print(sorted(users.Age.unique()))

Ok we have Outlier data in Age

In [ ]:
#lets find our unique value in location column

In [ ]:
users.Location.unique()

In [ ]:
users.Location.nunique()

57339 unique values, its really hard to understand
so lets create column Country

In [ ]:
for i in users :
    users['Country'] = users.Location.str.extract(r'\,+\s?(\w*\s?\w*)\"*$')

In [ ]:
users.Country.nunique()

In [ ]:
#drop location column
users.drop('Location',axis=1,inplace=True)

In [ ]:
users

In [ ]:
users.isnull().sum()

In [ ]:
users['Country'] = users['Country'].astype('str')

In [ ]:
a = list(users.Country.unique())
a =set(a)
a= list(a)
a = [x for x in a if x is not None]
a.sort()
print(a)

Some data has Misspellings , Lets correct it.

In [ ]:
users['Country'].replace(['','01776','02458','19104','23232','30064','85021','87510','alachua','america','austria','autralia','cananda','geermany','italia','united kindgonm','united sates','united staes','united state','united states','us'],
                           ['other','usa','usa','usa','usa','usa','usa','usa','usa','usa','australia','australia','canada','germany','italy','united kingdom','usa','usa','usa','usa','usa'],inplace=True)

In [ ]:
plt.figure(figsize=(15,7))
sns.countplot(y='Country',data=users,order=pd.value_counts(users['Country']).iloc[:10].index)
plt.title('Count of users Country wise')

Most number of users are from USA

In [ ]:
#Lets treat outliers in users age

In [ ]:
sns.distplot(users.Age)
plt.title('Age Distribution Plot')

Age value's below 5 and above 100 do not make much sense for our book rating case...hence replacing these by NaNs

In [ ]:
#Outlier data became NaN
users.loc[(users.Age > 100) | (users.Age < 5), 'Age'] = np.nan

In [ ]:
users.isna().sum()

Age has positive Skewness (right tail) so we can use median to fill Nan values, but for this we don't like to fill Nan value just for one range of age. To handle this we'll use country column to fill Nan.

In [ ]:
users['Age'] = users['Age'].fillna(users.groupby('Country')['Age'].transform('median'))

In [ ]:
users.isna().sum()

Still we have 276 Nan values let's fill them with mean

In [ ]:
users['Age'].fillna(users.Age.mean(), inplace=True)

In [ ]:
users.isna().sum()

# 2)Books_Dataset

In [ ]:
books

In [ ]:
books.head(2)

In [ ]:
#Top 10 Authors which have written the most books.

In [ ]:
plt.figure(figsize=(15,7))
sns.countplot(y='Book-Author',data=books,order=pd.value_counts(books['Book-Author']).iloc[:10].index)
plt.title('Top 10 Authors')

In [ ]:
#Top 10 Publisher which have published the most books

In [ ]:
plt.figure(figsize=(15,7))
sns.countplot(y='Publisher',data=books,order=pd.value_counts(books['Publisher']).iloc[:10].index)
plt.title('Top 10 Publishers')

In [ ]:
books['Year-Of-Publication']=books['Year-Of-Publication'].astype('str')
a=list(books['Year-Of-Publication'].unique())
a=set(a)
a=list(a)
a = [x for x in a if x is not None]
a.sort()
print(a)

In [ ]:
#investigating the rows having 'DK Publishing Inc' as year Of Publication
books.loc[books['Year-Of-Publication'] == 'DK Publishing Inc',:]

As it can be seen from above that there are some incorrect entries in Year-Of-Publication field. It looks like Publisher names 'DK Publishing Inc' and 'Gallimard' have been incorrectly loaded as Year-Of-Publication in dataset due to some errors in csv file

In [ ]:
#From above, it is seen that bookAuthor is incorrectly loaded with bookTitle, hence making required corrections
#ISBN '0789466953'
books.loc[books.ISBN == '0789466953','Year-Of-Publication'] = 2000
books.loc[books.ISBN == '0789466953','Book-Author'] = "James Buckley"
books.loc[books.ISBN == '0789466953','Publisher'] = "DK Publishing Inc"
books.loc[books.ISBN == '0789466953','Book-Title'] = "DK Readers: Creating the X-Men, How Comic Books Come to Life (Level 4: Proficient Readers)"

In [ ]:
#ISBN '078946697X'
books.loc[books.ISBN == '078946697X','Year-Of-Publication'] = 2000
books.loc[books.ISBN == '078946697X','Book-Author'] = "Michael Teitelbaum"
books.loc[books.ISBN == '078946697X','Publisher'] = "DK Publishing Inc"
books.loc[books.ISBN == '078946697X','Book-Title'] = "DK Readers: Creating the X-Men, How It All Began (Level 4: Proficient Readers)"

In [ ]:
#rechecking
books.loc[(books.ISBN == '0789466953') | (books.ISBN == '078946697X'),:]

In [ ]:
#investigating the rows having 'Gallimard' as yearOfPublication
books.loc[books['Year-Of-Publication'] == 'Gallimard',:]

In [ ]:
#making required corrections as above, keeping other fields intact
books.loc[books.ISBN == '2070426769','Year-Of-Publication'] = 2003
books.loc[books.ISBN == '2070426769','Book-Author'] = "Jean-Marie Gustave Le ClÃ?Â©zio"
books.loc[books.ISBN == '2070426769','Publisher'] = "Gallimard"
books.loc[books.ISBN == '2070426769','Book-Title'] = "Peuple du ciel, suivi de 'Les Bergers"


books.loc[books.ISBN == '2070426769',:]

In [ ]:
books['Year-Of-Publication']=pd.to_numeric(books['Year-Of-Publication'], errors='coerce')

print(sorted(books['Year-Of-Publication'].unique()))
#Now it can be seen that yearOfPublication has all values as integers

The value 0 for Year-Of_Publication is invalid and as this dataset was published in 2004, We have assumed that the years after 2006 to be invalid and setting invalid years as NaN

Reference of the fact: http://www2.informatik.uni-freiburg.de/~cziegler/BX/

In [ ]:
books.loc[(books['Year-Of-Publication'] > 2006) | (books['Year-Of-Publication'] == 0),'Year-Of-Publication'] = np.NAN

#replacing NaNs with median value of Year-Of-Publication
books['Year-Of-Publication'].fillna(round(books['Year-Of-Publication'].median()), inplace=True)

In [ ]:
#dropping last three columns containing image URLs which will not be required for analysis
books.drop(['Image-URL-S', 'Image-URL-M', 'Image-URL-L'],axis=1,inplace=True)

In [ ]:
books.isna().sum()

In [ ]:
#exploring 'publisher' column
books.loc[books.Publisher.isnull(),:]

In [ ]:
#Filling Nan of Publisher with others
books.Publisher.fillna('other',inplace=True)

In [ ]:
#exploring 'Book-Author' column
books.loc[books['Book-Author'].isnull(),:]

In [ ]:
#Filling Nan of Book-Author with others
books['Book-Author'].fillna('other',inplace=True)

In [ ]:
books.isna().sum()

# 3) Ratings Dataset

In [ ]:
ratings

Ratings dataset should have books only which exist in our books dataset

In [ ]:
ratings_new = ratings[ratings.ISBN.isin(books.ISBN)]
ratings.shape, ratings_new.shape

It can be seen that many rows having book ISBN not part of books dataset got dropped off

Ratings dataset should have ratings from users which exist in users dataset.



In [ ]:
print("Shape of dataset before dropping",ratings_new.shape)
ratings_new = ratings_new[ratings_new['User-ID'].isin(users['User-ID'])]
print("shape of dataset after dropping",ratings_new.shape)

It can be seen that no new user was there in ratings dataset.

Let's see how the ratings are distributed

In [ ]:
plt.rc("font", size=15)
ratings_new['Book-Rating'].value_counts(sort=False).plot(kind='bar')
plt.title('Rating Distribution\n')
plt.xlabel('Rating')
plt.ylabel('Count')
plt.show()

The ratings are very unevenly distributed, and the vast majority of ratings are 0 .As quoted in the description of the dataset - BX-Book-Ratings contains the book rating information. Ratings are either explicit, expressed on a scale from 1-10 higher values denoting higher appreciation, or implicit, expressed by 0.Hence segragating implicit and explict ratings datasets

In [ ]:
#Hence segragating implicit and explict ratings datasets
ratings_explicit = ratings_new[ratings_new['Book-Rating'] != 0]
ratings_implicit = ratings_new[ratings_new['Book-Rating'] == 0]

In [ ]:
print('ratings_explicit dataset',ratings_explicit.shape)
print('ratings_implicit dataset',ratings_implicit.shape)

In [ ]:
plt.style.use('fivethirtyeight')
plt.figure(figsize=(12, 8))
sns.countplot(data=ratings_explicit , x='Book-Rating', palette='rocket_r')

It can be observe that higher ratings are more common amongst users and rating 8 has been rated highest number of times

In [ ]:
#Let's find the top 5 books which are rated by most number of users.
rating_count = pd.DataFrame(ratings_explicit.groupby('ISBN')['Book-Rating'].count())
rating_count.sort_values('Book-Rating', ascending=False).head()

The book with ISBN '0316666343' received the most rating counts.

In [ ]:
#Let’s find out what book it is, and what books are in the top 5.
most_rated_books = pd.DataFrame(['0316666343', '0971880107', '0385504209', '0312195516', '0060928336'], index=np.arange(5), columns = ['ISBN'])
most_rated_books_summary = pd.merge(most_rated_books, books, on='ISBN')
most_rated_books_summary

The book that received the most rating counts in this data set is Rich Shapero’s “Wild Animus”. And there is something in common among these five books that received the most rating counts — they are all novels. So it is conclusive that novels are popular and likely receive more ratings.

In [ ]:
#create column Rating Average
ratings_explicit ['Avg_Rating'] = ratings_explicit.groupby('ISBN')['Book-Rating'].transform('mean')

In [ ]:
#Cearting column Rating sum
ratings_explicit['Total_No_Of_Users_Rated']=ratings_explicit.groupby('ISBN')['Book-Rating'].transform('count')

In [ ]:
ratings_explicit

# Merging All Dataset

In [ ]:
Final_Dataset=users.copy()
Final_Dataset=pd.merge(Final_Dataset,ratings_explicit,on='User-ID')
Final_Dataset=pd.merge(Final_Dataset,books,on='ISBN')

In [ ]:
Final_Dataset

In [ ]:
missing_values(Final_Dataset)

In [ ]:
Final_Dataset.shape

# Collaborative Filtering based Recommendation System

In [ ]:
Final_Dataset

In [ ]:
x = Final_Dataset.groupby('User-ID').count()['Book-Rating'] >50
y = x[x].index

In [ ]:
x

In [ ]:
y

In [ ]:
filtered_rating = Final_Dataset[Final_Dataset['User-ID'].isin(y)]

In [ ]:
filtered_rating

In [ ]:
y1 = filtered_rating.groupby('Book-Title').count()['Book-Rating']>= 10
famous_books = y1[y1].index

In [ ]:
famous_books

In [ ]:
final_ratings = filtered_rating[filtered_rating['Book-Title'].isin(famous_books) ]
final_ratings

In [ ]:
final_ratings['User-ID'].nunique()

# Item- Item Based Filtering

In [ ]:
pt = final_ratings.pivot_table(index='Book-Title',columns='User-ID',values='Book-Rating')

In [ ]:
pt

In [ ]:
pt.fillna(0,inplace=True)

In [ ]:
pt

In [ ]:
#Calculate the distances and similarity

In [ ]:
from sklearn.metrics import pairwise_distances

In [ ]:
pd.DataFrame(pairwise_distances(pt, metric='cosine'))

In [ ]:
sim = 1- pairwise_distances(pt, metric='cosine')
pd.DataFrame(sim)

In [ ]:
np.fill_diagonal(sim,0)

In [ ]:
similarity_item = pd.DataFrame(sim)
similarity_item

In [ ]:
similarity_item.index = final_ratings['Book-Title'].unique()
similarity_item.columns = final_ratings['Book-Title'].unique()

In [ ]:
pd.set_option('display.max_columns', None)

In [ ]:
similarity_item

In [ ]:
#Find out similar users

In [ ]:
similarity_item.idxmax()

Beloved (Plume Contemporary Fiction)                                                               The Lake House
Airframe                                                                                 Angela's Ashes: A Memoir
Piercing the Darkness                                            The Book of Ruth (Oprah's Book Club (Paperback))
To Kill a Mockingbird                                           The Ritual Bath (Peter Decker &amp; Rina Lazar...
Seabiscuit: An American Legend                                                                         The Hobbit
                                                                                      ...                        
Rilla of Ingleside (Anne of Green Gables Novels (Paperback))                                           Back Roads
Loyalty in Death                                                                            It's Always Something
After Twilight                                                                          

In [ ]:
from sklearn.metrics.pairwise import cosine_similarity

In [ ]:
similarity_item_scores=cosine_similarity(pt)

In [ ]:
similarity_item_scores[0]

array([1.        , 0.07808466, 0.07799952, ..., 0.06345498, 0.09145795,
       0.05094141])

In [ ]:
similarity_item_scores.shape

(1697, 1697)

In [ ]:
def recommend_for_item(book_name):
    index=np.where(pt.index==book_name)[0][0]
    distances=similarity_item_scores[index]
    similar_items=sorted(list(enumerate(similarity_item_scores[index])),key=lambda x:x[1], reverse=True)[1:11]
    data=[]
    for i in similar_items:
        item=[]
        temp_df = books[books['Book-Title'] == pt.index[i[0]]]
        item.extend(list(temp_df.drop_duplicates('Book-Title')['Book-Title'].values))
        item.extend(list(temp_df.drop_duplicates('Book-Title')['Book-Author'].values))

        data.append(item)
    return data

In [ ]:
recommend_for_item('The Notebook')

[['Nights in Rodanthe', 'Nicholas Sparks'],
 ['A Walk to Remember', 'Nicholas Sparks'],
 ['The Rescue', 'Nicholas Sparks'],
 ['The Five People You Meet in Heaven', 'Mitch Albom'],
 ["Suzanne's Diary for Nicholas", 'James Patterson'],
 ['Book Club', 'Mary Alice Monroe'],
 ['Message in a Bottle', 'Nicholas Sparks'],
 ['One Door Away from Heaven', 'Dean R. Koontz'],
 ['While I Was Gone', 'Sue Miller'],
 ['The Ranch', 'DANIELLE STEEL']]

# User-User Based Filtering

In [ ]:
final_ratings

User-ID   Age    Country        ISBN  Book-Rating  Avg_Rating  \
19         6242  33.0     canada  0452264464            5    7.772152   
22        11676  28.0        nan  0452264464            8    7.772152   
27        22625  54.0        usa  0452264464            9    7.772152   
31        36907  39.0     canada  0452264464           10    7.772152   
36        58363  81.0        usa  0452264464            5    7.772152   
...         ...   ...        ...         ...          ...         ...   
381804   270820  52.0        usa  0606298347            7    7.000000   
382030   271705  25.0        usa  0613212320           10   10.000000   
382625   274061  26.0        usa  1551663147           10   10.000000   
382739   274301  41.0  australia  0449000729           10   10.000000   
383149   275970  46.0        usa  1586210661            9    9.000000   

        Total_No_Of_Users_Rated                            Book-Title  \
19                           79  Beloved (Plume Contemporary Fiction)   
22                           79  Beloved (Plume Contemporary Fiction)   
27                           79  Beloved (Plume Contemporary Fiction)   
31                           79  Beloved (Plume Contemporary Fiction)   
36                           79  Beloved (Plume Contemporary Fiction)   
...                         ...                                   ...   
381804                        1                            The Vision   
382030                        1              Blindness (Harvest Book)   
382625                        1                                 Fever   
382739                        1           Sarum: The Novel of England   
383149                        1                Me Talk Pretty One Day   

              Book-Author  Year-Of-Publication  \
19          Toni Morrison               1994.0   
22          Toni Morrison               1994.0   
27          Toni Morrison               1994.0   
31          Toni Morrison               1994.0   
36          Toni Morrison               1994.0   
...                   ...                  ...   
381804     Dean R. Koontz               1986.0   
382030      Jose Saramago               2000.0   
382625   Elizabeth Lowell               1997.0   
382739  Edward Rutherfurd               1997.0   
383149      David Sedaris               2001.0   

                                          Publisher  
19                                            Plume  
22                                            Plume  
27                                            Plume  
31                                            Plume  
36                                            Plume  
...                                             ...  
381804  Turtleback Books Distributed by Demco Media  
382030                              Sagebrush Bound  
382625                                         Mira  
382739                             Ballantine Books  
383149                      Time Warner Audio Major  

[32276 rows x 11 columns]

In [ ]:
pt2 = final_ratings.pivot_table(index='User-ID',columns='Book-Title',values='Book-Rating')

In [ ]:
pt2

Book-Title  1984  1st to Die: A Novel  2010: Odyssey Two  2061: Odyssey Three  \
User-ID                                                                         
254          9.0                  NaN                NaN                  NaN   
638          NaN                  NaN                NaN                  NaN   
1424         NaN                  NaN                NaN                  NaN   
1733         NaN                  NaN                NaN                  NaN   
1903         NaN                  NaN                NaN                  NaN   
...          ...                  ...                ...                  ...   
276680       NaN                  NaN                NaN                  NaN   
277427       NaN                  NaN                NaN                  NaN   
278137       NaN                  NaN                NaN                  NaN   
278188       NaN                  NaN                NaN                  NaN   
278418       NaN                  NaN                NaN                  NaN   

Book-Title  2nd Chance  311 Pelican Court  3rd Degree  4 Blondes  \
User-ID                                                            
254                NaN                NaN         NaN        NaN   
638                9.0                NaN         NaN        NaN   
1424               NaN                NaN         NaN        NaN   
1733               NaN                NaN         NaN        NaN   
1903               NaN                NaN         NaN        NaN   
...                ...                ...         ...        ...   
276680             NaN                NaN         NaN        NaN   
277427             NaN                NaN         NaN        NaN   
278137             NaN                NaN         NaN        NaN   
278188             NaN                NaN         NaN        NaN   
278418             NaN                NaN         NaN        NaN   

Book-Title  84 Charing Cross Road  \
User-ID                             
254                           NaN   
638                           NaN   
1424                          NaN   
1733                          NaN   
1903                          NaN   
...                           ...   
276680                        NaN   
277427                        NaN   
278137                        NaN   
278188                        NaN   
278418                        NaN   

Book-Title  A 2nd Helping of Chicken Soup for the Soul (Chicken Soup for the Soul Series (Paper))  \
User-ID                                                                                             
254                                                       NaN                                       
638                                                       NaN                                       
1424                                                      NaN                                       
1733                                                      NaN                                       
1903                                                      NaN                                       
...                                                       ...                                       
276680                                                    NaN                                       
277427                                                    NaN                                       
278137                                                    NaN                                       
278188                                                    NaN                                       
278418                                                    NaN                                       

Book-Title  A Beautiful Mind: The Life of Mathematical Genius and Nobel Laureate John Nash  \
User-ID                                                                                      
254                                                       NaN                

In [ ]:
pt2.fillna(0,inplace=True)

In [ ]:
pt2

Book-Title  1984  1st to Die: A Novel  2010: Odyssey Two  2061: Odyssey Three  \
User-ID                                                                         
254          9.0                  0.0                0.0                  0.0   
638          0.0                  0.0                0.0                  0.0   
1424         0.0                  0.0                0.0                  0.0   
1733         0.0                  0.0                0.0                  0.0   
1903         0.0                  0.0                0.0                  0.0   
...          ...                  ...                ...                  ...   
276680       0.0                  0.0                0.0                  0.0   
277427       0.0                  0.0                0.0                  0.0   
278137       0.0                  0.0                0.0                  0.0   
278188       0.0                  0.0                0.0                  0.0   
278418       0.0                  0.0                0.0                  0.0   

Book-Title  2nd Chance  311 Pelican Court  3rd Degree  4 Blondes  \
User-ID                                                            
254                0.0                0.0         0.0        0.0   
638                9.0                0.0         0.0        0.0   
1424               0.0                0.0         0.0        0.0   
1733               0.0                0.0         0.0        0.0   
1903               0.0                0.0         0.0        0.0   
...                ...                ...         ...        ...   
276680             0.0                0.0         0.0        0.0   
277427             0.0                0.0         0.0        0.0   
278137             0.0                0.0         0.0        0.0   
278188             0.0                0.0         0.0        0.0   
278418             0.0                0.0         0.0        0.0   

Book-Title  84 Charing Cross Road  \
User-ID                             
254                           0.0   
638                           0.0   
1424                          0.0   
1733                          0.0   
1903                          0.0   
...                           ...   
276680                        0.0   
277427                        0.0   
278137                        0.0   
278188                        0.0   
278418                        0.0   

Book-Title  A 2nd Helping of Chicken Soup for the Soul (Chicken Soup for the Soul Series (Paper))  \
User-ID                                                                                             
254                                                       0.0                                       
638                                                       0.0                                       
1424                                                      0.0                                       
1733                                                      0.0                                       
1903                                                      0.0                                       
...                                                       ...                                       
276680                                                    0.0                                       
277427                                                    0.0                                       
278137                                                    0.0                                       
278188                                                    0.0                                       
278418                                                    0.0                                       

Book-Title  A Beautiful Mind: The Life of Mathematical Genius and Nobel Laureate John Nash  \
User-ID                                                                                      
254                                                       0.0                

In [ ]:
#Calculating distance and Similarity

In [ ]:
pd.DataFrame(pairwise_distances(pt2, metric='cosine'))

0             1             2     3         4         5     \
0     1.110223e-16  1.000000e+00  1.000000e+00   1.0  1.000000  0.816938   
1     1.000000e+00  2.220446e-16  9.418335e-01   1.0  0.917313  1.000000   
2     1.000000e+00  9.418335e-01  1.110223e-16   1.0  1.000000  1.000000   
3     1.000000e+00  1.000000e+00  1.000000e+00   0.0  1.000000  1.000000   
4     1.000000e+00  9.173135e-01  1.000000e+00   1.0  0.000000  0.899269   
...            ...           ...           ...   ...       ...       ...   
1123  1.000000e+00  9.341138e-01  1.000000e+00   1.0  1.000000  1.000000   
1124  1.000000e+00  9.141963e-01  1.000000e+00   1.0  1.000000  1.000000   
1125  1.000000e+00  9.394233e-01  9.133642e-01   1.0  1.000000  0.966792   
1126  1.000000e+00  1.000000e+00  1.000000e+00   1.0  1.000000  1.000000   
1127  1.000000e+00  9.491691e-01  1.000000e+00   1.0  1.000000  1.000000   

          6         7         8         9         10    11        12    \
0     1.000000  1.000000  1.000000  0.945014  0.930199   1.0  0.816586   
1     1.000000  0.932186  0.895561  1.000000  1.000000   1.0  1.000000   
2     1.000000  1.000000  0.931995  0.940890  0.912460   1.0  1.000000   
3     0.862147  1.000000  0.994684  1.000000  1.000000   1.0  1.000000   
4     1.000000  1.000000  1.000000  1.000000  1.000000   1.0  1.000000   
...        ...       ...       ...       ...       ...   ...       ...   
1123  1.000000  1.000000  0.928667  0.946437  1.000000   1.0  1.000000   
1124  1.000000  1.000000  1.000000  0.950953  1.000000   1.0  1.000000   
1125  1.000000  1.000000  1.000000  0.917922  1.000000   1.0  1.000000   
1126  1.000000  1.000000  1.000000  1.000000  1.000000   1.0  1.000000   
1127  1.000000  1.000000  0.963889  1.000000  1.000000   1.0  1.000000   

          13        14    15    16        17        18        19        20    \
0     0.876007  1.000000   1.0   1.0  0.960021  1.000000  1.000000  0.875671   
1     1.000000  0.891638   1.0   1.0  1.000000  0.969502  0.900330  0.976119   
2     1.000000  0.974606   1.0   1.0  1.000000  1.000000  0.947764  1.000000   
3     1.000000  1.000000   1.0   1.0  1.000000  1.000000  1.000000  1.000000   
4     1.000000  1.000000   1.0   1.0  1.000000  1.000000  1.000000  1.000000   
...        ...       ...   ...   ...       ...       ...       ...       ...   
1123  1.000000  0.952347   1.0   1.0  1.000000  1.000000  0.980277  0.960507   
1124  1.000000  0.975417   1.0   1.0  0.975346  1.000000  1.000000  0.944818   
1125  0.931754  1.000000   1.0   1.0  0.966432  1.000000  1.000000  0.948128   
1126  1.000000  0.949255   1.0   1.0  1.000000  1.000000  1.000000  1.000000   
1127  1.000000  1.000000   1.0   1.0  1.000000  1.000000  1.000000  0.951637   

      21        22        23        24        25        26        27    \
0      1.0  0.962189  0.911947  0.959825  1.000000  1.000000  1.000000   
1      1.0  1.000000  0.930377  0.902887  1.000000  0.821407  1.000000   
2      1.0  1.000000  0.963697  0.941725  0.940105  1.000000  1.000000   
3      1.0  1.000000  0.946190  1.000000  0.973247  1.000000  1.000000   
4      1.0  1.000000  1.000000  1.000000  1.000000  1.000000  1.000000   
...    ...       ...       ...       ...       ...       ...       ...   
1123   1.0  0.974536  0.982090  0.963514  0.943463  1.000000  1.000000   
1124   1.0  0.953366  1.000000  0.896302  1.000000  1.000000  0.919699   
1125   1.0  1.000000  0.966394  0.949327  1.000000  1.000000  1.000000   
1126   1.0  0.973678  1.000000  1.000000  1.000000  1.000000  1.000000   
1127   1.0  1.000000  1.000000  1.000000  1.000000  1.000000  1.000000   

          28        29        30        31        32        33        34    \
0     0.905240  1.000000  0.930289  1.000000  0.969753  0.935781  0.921170   
1     0.987382  0.949326  1.000000  0.969074  0.933095  0.895108  0.950341   
2     0.970998  1.000000  1.000000  1.000000  0.957324  0.916138  0.967045   
3     1.000000  1.000000  1.000000  0.966387  1.00

In [ ]:
sim2 = 1- pairwise_distances(pt2, metric='cosine')
pd.DataFrame(sim2)

In [ ]:
np.fill_diagonal(sim2,0)

In [ ]:
similarity_user = pd.DataFrame(sim2)

In [ ]:
similarity_user.index = final_ratings['User-ID'].unique()
similarity_user.columns = final_ratings['User-ID'].unique()

In [ ]:
similarity_user

In [ ]:
#Finind similar user

In [ ]:
similarity_user.idxmax()

In [ ]:
final_ratings[(final_ratings['User-ID'] == 72352) | (final_ratings['User-ID'] == 132492)]

In [ ]:
similarity_user_score = cosine_similarity(pt2)

In [ ]:
similarity_user_score[0]

In [ ]:
def recommendations_for_user(user_id):
    print('\n Recommended Books for User_id',(user_id),':\n')
    recom = list(similarity_user.sort_values([user_id], ascending= False).head().index)[1:11]
    books_list = []
    for i in recom:
        books_list = books_list + list(final_ratings[final_ratings['User-ID']==i]['Book-Title'])
    return set(books_list)-set(final_ratings[final_ratings['User-ID']==user_id]['Book-Title'])

In [ ]:
recommendations_for_user(6242)

# Model Evaluation

In [ ]:
#Train-Test Split
from sklearn import model_selection
train_data, test_data = model_selection.train_test_split(final_ratings, test_size=0.20)

In [ ]:
print(f'Training set lengths: {len(train_data)}')
print(f'Testing set lengths: {len(test_data)}')
print(f'Test set is {(len(test_data)/(len(train_data)+len(test_data))*100):.0f}% of the full dataset.')

In [ ]:
# Get int mapping for user_id in train dataset
u_unique_train = train_data['User-ID'].unique()
train_data_user2idx = {o:i for i, o in enumerate(u_unique_train)}

# Get int mapping for isbn in train dataset
i_unique_train = train_data['ISBN'].unique()
train_data_book2idx = {o:i for i, o in enumerate(i_unique_train)}

In [ ]:
# Get int mapping for user_id in test dataset
u_unique_test = test_data['User-ID'].unique()
test_data_user2idx = {o:i for i, o in enumerate(u_unique_test)}

# Get int mapping for isbn in test dataset
i_unique_test = test_data['ISBN'].unique()
test_data_book2idx = {o:i for i, o in enumerate(i_unique_test)}

In [ ]:
# training set
train_data['u_unique'] = train_data['User-ID'].map(train_data_user2idx)
train_data['i_unique'] = train_data['ISBN'].map(train_data_book2idx)

# testing set
test_data['u_unique'] = test_data['User-ID'].map(test_data_user2idx)
test_data['i_unique'] = test_data['ISBN'].map(test_data_book2idx)

# Convert back to three feature of dataframe
train_data = train_data[['u_unique', 'i_unique', 'Book-Rating']]
test_data = test_data[['u_unique', 'i_unique', 'Book-Rating']]

In [ ]:
train_data.sample(2)

In [ ]:
test_data.sample(2)

In [ ]:
# User-Item for Train Data

In [ ]:
# first I'll create an empty matrix of users books and then I'll add the appropriate values to the matrix by extracting them from the dataset
n_users = train_data['u_unique'].nunique()
n_books = train_data['i_unique'].nunique()

train_matrix = np.zeros((n_users, n_books))

for entry in train_data.itertuples():
    train_matrix[entry[1]-1, entry[2]-1] = entry[3]
    # entry[1] is the user-id, entry[2] is the book-isbn and -1 is to counter 0-based indexing

In [ ]:
train_matrix.shape

In [ ]:
# User-Item for Test Data]

In [ ]:
n_users = test_data['u_unique'].nunique()
n_books = test_data['i_unique'].nunique()

test_matrix = np.zeros((n_users, n_books))

for entry in test_data.itertuples():
    test_matrix[entry[1]-1, entry[2]-1] = entry[3]

In [ ]:
test_matrix.shape

# Cosine Similarity Based Recommendation System

In [ ]:
train_matrix_small = train_matrix[:1000, :1000]
test_matrix_small = test_matrix[:1000, :1000]

from sklearn.metrics.pairwise import pairwise_distances
user_similarity = pairwise_distances(train_matrix_small, metric='cosine')
item_similarity = pairwise_distances(train_matrix_small.T, metric='cosine')

In [ ]:
# function to predict the similarity :
def predict_books(ratings, similarity, type='user'): # default type is 'user'
    if type == 'user':
        mean_user_rating = ratings.mean(axis=1)

        # Use np.newaxis so that mean_user_rating has the same format as ratings
        ratings_diff = (ratings - mean_user_rating[:, np.newaxis])
        pred = mean_user_rating[:, np.newaxis] + similarity.dot(ratings_diff) / np.array([np.abs(similarity).sum(axis=1)]).T
    elif type == 'item':
        pred = ratings.dot(similarity) / np.array([np.abs(similarity).sum(axis=1)])
    return pred

In [ ]:
item_prediction = predict_books(train_matrix_small, item_similarity , type='item')
user_prediction = predict_books(train_matrix_small, user_similarity , type='user')

# Evaluation Metric

In [ ]:
# Evaluation metric by mean squared error
from sklearn.metrics import mean_squared_error
from math import sqrt

def rmse(prediction, test_matrix):
    prediction = prediction[test_matrix.nonzero()].flatten()
    test_matrix = test_matrix[test_matrix.nonzero()].flatten()
    return sqrt(mean_squared_error(prediction, test_matrix))

print(f'Item-based CF RMSE: {rmse(item_prediction, test_matrix_small)}')
print(f'User-based CF RMSE: {rmse(user_prediction, test_matrix_small)}')

In [ ]:
## Let's go through Model based approach by SVD model.

In [ ]:
!pip install scikit-surprise

In [ ]:
from surprise import Reader, Dataset

In [ ]:
# Creating a 'Reader' object to set the limit of the ratings
reader = Reader(rating_scale=(1, 10))
data = Dataset.load_from_df(final_ratings[['User-ID','Book-Title','Book-Rating']], reader)

In [ ]:
from surprise import SVD, model_selection, accuracy
model = SVD()

# Train on books dataset
%time model_selection.cross_validate(model, data, measures=['RMSE'], cv=5, verbose=True)

# Train - Test Split

In [ ]:
# train and test split
trainset, testset = model_selection.train_test_split(data, test_size=0.2)

# SVD model
model = SVD()
model.fit(trainset)

In [ ]:
trainset()


# Evaluation metrics for SVD model

In [ ]:
# displaying RMSE score
predictions = model.test(testset)
print(f"The accuracy is {accuracy.rmse(predictions)}")

# Testing Results

In [ ]:
# to test result let's take an user-id and item-id to test our model.
uid = 276744
iid = '038550120X'
pred = model.predict(uid, iid, verbose=True)

In [ ]:
# display estimated rating and real rating
print(f'The estimated rating for the book with ISBN code {pred.iid} from user #{pred.uid} is {pred.est:.2f}.\n')
actual_rtg= ratings_explicit[(ratings_explicit['User-ID']==pred.uid) &
                             (ratings_explicit['ISBN']==pred.iid)]['Book-Rating'].values[0]
print(f'The real rating given for this was {actual_rtg:.2f}.')